In [1]:
#importing packages
from bs4 import BeautifulSoup 
import requests  
import json
from lxml import html

#URL for web scraping
url = 'https://fantasydata.com/nfl/fantasy-football-leaders?season=2022&seasontype=1&scope=1&subscope=1&aggregatescope=1&range=3'
 
# get player hyperlinks ot their page for individualized data
response = requests.get(url)
content = response.content
soup = BeautifulSoup(content, 'html.parser')
#gets stat table with player data
table = soup.findAll("table", {'id': 'stats_grid'})
#get player hyperlink
rows = table[0].findAll('a')

#group links to only grab player url not teams
links = []
for index, val in enumerate(rows):
    if(index % 2 != 0):
        continue
    else:
        link = val.get('href')
        links.append(link)

#get full link to recall urls based on player
newURLs = []
for link in links:
    #check last character to see if it is a player id or team id.
    #if team id skip
    if(link[-1].isnumeric()):
        newURL = "https://fantasydata.com" + link
        newURLs.append(newURL)

#grab player data from their weekly stats (for prior years as well)
playersJson = [];
for playerPage in newURLs:
    playerResponse = requests.get(playerPage)
    playerContent = playerResponse.content
    playerSoup = BeautifulSoup(playerContent, 'html.parser')
    
    #where current data is held for player
    allData = playerSoup.find_all('script')[44]

    jsonObj = None
    #variable player data json is held
    if allData.contents and "var all = " in allData.contents[0]:
        jsonStr = allData.contents[0]
        jsonStr = jsonStr.split("var all = ")[1].split(";", 1)[0]
        json_data = json.dumps(jsonStr)
        jsonObj = json.loads(json_data)
    
    #append players stats to array to manipulate later
    playersJson.append(jsonObj);


print(playersJson);



#print(table)

['[{"Key":2022,"Value":[{"PlayerID":19781,"Season":2022,"Played":1,"Started":1,"Week":1,"Opponent":"NYJ","TeamHasPossession":false,"HomeOrAway":"AWAY","TeamIsHome":false,"Result":null,"HomeScore":null,"AwayScore":null,"Quarter":null,"QuarterDisplay":null,"IsGameOver":true,"GameDate":"2022-09-11T13:00:00","TimeRemaining":null,"ScoreSummary":null,"PassingCompletions":17.00,"PassingAttempts":30.00,"PassingCompletionPercentage":56.7,"PassingYards":213.00,"PassingYardsPerAttempt":7.1,"PassingTouchdowns":3.00,"PassingInterceptions":1.00,"PassingRating":98.33,"RushingAttempts":6.00,"RushingYards":17.00,"RushingYardsPerAttempt":2.8,"RushingTouchdowns":0.00,"Receptions":0.00,"ReceivingTargets":0.00,"ReceivingYards":0.00,"ReceptionPercentage":0.0,"ReceivingTouchdowns":0.00,"ReceivingLong":0.00,"ReceivingYardsPerTarget":0.0,"ReceivingYardsPerReception":0.0,"Fumbles":0.00,"FumblesLost":0.00,"FieldGoalsMade":0.00,"FieldGoalsAttempted":0.00,"FieldGoalPercentage":0.0,"FieldGoalsLongestMade":0.00,"Ext